(rawdata)=
# Datos sin preprocesar
Los dos conjuntos de datos utilizados en este trabajo, como se explica en la {numref}`datos`, poseen señales similares de nueva física, que se diferencian por las masas de las partículas BSM y las fracción de eventos de señal. En esta sección se realizará una breve exploración de los datos R&D y BB1 publicados para las LHCO 2020. 

```{figure} ./../../figuras/lhco-RnD.png
---
name: rawdata-senal
figclass: margin
---
Diagrama de Feynmann para la señal.
```
Para esta sección, utilizamos los primeros 100,000 eventos de cada conjunto de datos por dos razones: utilizar todos los eventos no es posible porque requiere una gran cantidad de memoria y 100,000 eventos son suficientes para observar las distribuciones de los datos. Los datos utilizados representan el 9% y el 10% de los eventos del conjunto R&D y BB1, respectivamente, y poseen la misma proporción de señal y fondo que cada uno de los conjuntos en su totalidad.

In [1]:
# Importamos las librerías principales
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from myst_nb import glue
from PIL import Image
import os

# Funciones de benchtools
from benchtools.src.datatools import ascii_column
from benchtools.src.plotools import bkg_sig_hist, create_png, image_grid

# Definimos variables globales
PATH_IMAGES = '../../figuras/'

(rawdata-estruc)=
## Estructura
El conjunto de datos R&D y BB1 publicados para las olimpiadas posee un evento por fila, con la información de $pT$, $\eta$ y $\phi$ para cada hadrón del evento, como se muestra en {numref}`rawdata-rawdataframe`. La diferencia estructural entre ambos archivos es que el conjunto R&D tiene la etiqueta del evento en la última columna (señal o fondo), mientras que para el conjunto BB1 la etiqueta se encuentra en un archivo aparte.

```{table} Estructura del conjunto de datos R&D. Cada fila es un evento y la última columna hace referencia a si el evento es fondo (0) o señal (1).
:name: rawdata-rawdataframe
|Evento   |$pT$     | $\eta$  | $\phi$  | $pT$    | $\eta$  | $\phi$  | $\cdots$| señal |
|---------|---------|---------|---------|---------|---------|---------|---------|-------|
| 1       | $\cdots$| $\cdots$| $\cdots$| $\cdots$| $\cdots$| $\cdots$| $\cdots$| 1.0   |
| 2       | $\cdots$| $\cdots$| $\cdots$| $\cdots$| $\cdots$| $\cdots$| $\cdots$| 0.0   |
| $\vdots$| $\cdots$| $\cdots$| $\cdots$| $\cdots$| $\cdots$| $\cdots$| $\cdots$| 0.0   |
```
El conjunto R&D posee 1,000,000 de eventos de fondo y 100,000 de señal (aproximadamente 9.09% de los eventos son señal). En este conjunto las partículas $Z'$, $X$ y $Y$ tienen masas de 3.5 TeV, 500 GeV y 100 GeV, respectivamente. En el conjunto BB1, las partículas $Z'$, $X$ y $Y$ tienen masas de 3,823 TeV, 732 GeV y 378 GeV, respectivamente, con un porcentaje menor de señal: de 1,000,000 de eventos, 834 son señal, es decir, el 0.08% es señal, como se discutió en la {numref}`datos`.

La información de los primeros 5 eventos del conjunto R&D se puede observar en la {numref}`df-raw`.

In [2]:
# Cargamos 100,000 eventos
path_data = "../../../datos/events_anomalydetection.h5"
df_RnD = pd.read_hdf(path_data, stop=100000)
glue("df-raw", df_RnD.head(), display=False)

```{glue:figure} df-raw
:figwidth: 600px
:name: "df-raw"

Primeros 5 eventos de los datos R&D. Cada fila representa un evento y cada columna representa una medida de la cinemática de un hadrón, como se muestra en la {numref}`rawdata-rawdataframe`. La columna 2100 representa la etiqueta del evento (señal o fondo).
```

Cada evento tiene un número distinto de hadrones. Por ejemplo, los primeros eventos del conjunto R&D tienen:

In [3]:
# Eliminamos la señal para evitar contar los hadrónes
ns_df_RnD = df_RnD.iloc[:,:-1]  

# Contamos los valores de pT distintos de cero
df_RnD['n_hadrons'] = ns_df_RnD.iloc[:,::3].gt(0).sum(axis='columns')

# Imprimimos para los primeros 5 eventos    
for event in range(5):
    print("Evento {}: {} hadrones".format(event, df_RnD.loc[event,'n_hadrons']))

Evento 0: 109 hadrones
Evento 1: 208 hadrones
Evento 2: 196 hadrones
Evento 3: 183 hadrones
Evento 4: 169 hadrones


(rawdata-dist)=
## Distribuciones
Para ambos conjuntos, las distribuciones de los datos son similares. La diferencia más evidente es la proporción de eventos de señal, que requiere de histogramas con menos contenedores para el conjunto con menor proporción de señal, es decir, para el conjunto BB1.

In [4]:
# Cargamos 100,000 eventos de los datos BB1 
df_BB1_nk = pd.read_hdf('../../../datos/events_LHCO2020_BlackBox1.h5', stop=100000)
# Cargamos las estiquetas
df_key = ascii_column('../../../datos/events_LHCO2020_BlackBox1.masterkey', column_name=2100)
# Juntamos los dataframes
df_BB1 = pd.concat([df_BB1_nk, df_key.iloc[:100000]], axis=1, sort=False)
# Contamos el numero de hadrónes
# Eliminamos la señal para evitar contar los hadrónes
ns_df_BB1 = df_BB1.iloc[:,:-1]  
df_BB1['n_hadrons'] = ns_df_BB1.iloc[:,::3].gt(0).sum(axis='columns')

In [5]:
for name, df in zip(['R&D', 'BB1'], [df_RnD,df_BB1]):
    # Graficamos utilizando benchtools
    fig = plt.figure(facecolor='white', figsize=(6,8));
    bkg_sig_hist(df, variable='n_hadrons', label=2100, xlabel='Nro. de hadrones', ylabel='Densidad de eventos' , n_bins=20); # label=2100 porque esa es la columna de señal
    plt.title('Nro. hadrones {}'.format(name))
    plt.savefig(os.path.join('../../figuras/','rawdata-{}-nhadrons.png'.format(name)), bbox_inches='tight', facecolor=fig.get_facecolor(),edgecolor='none')
    plt.clf()

# Creamos un grid de las imagenes usando benchtools
imagenes = ['./../../figuras/rawdata-R&D-nhadrons.png', './../../figuras/rawdata-BB1-nhadrons.png']
image_grid(rows=1, columns=2, images=imagenes, name='rawdata-nhadrones', path=PATH_IMAGES, remove=True)

<Figure size 432x576 with 0 Axes>

<Figure size 432x288 with 0 Axes>

<Figure size 432x576 with 0 Axes>

<Figure size 432x288 with 0 Axes>

```{figure} ./../../figuras/rawdata-nhadrones.png
---
name: rawdata-nhadrones
width: 80%
---
Distribución del número de hadrones para eventos de señal y fondo. A la izquierda el conjunto R&D y a la derecha el conjunto BB1.
```

In [6]:
# En esta celda calculamos la media del numero de hadrónes de la figura anterior
# Señal
mean_nhad_RnD_sig = df_RnD.loc[df_RnD[2100]==1]['n_hadrons'].mean()
mean_nhad_BB1_sig = df_BB1.loc[df_BB1[2100]==1]['n_hadrons'].mean()
# Fondo
mean_nhad_RnD_bkg = df_RnD.loc[df_RnD[2100]==0]['n_hadrons'].mean()
mean_nhad_BB1_bkg = df_BB1.loc[df_BB1[2100]==0]['n_hadrons'].mean()

glue("mean_nhad_RnD_sig", mean_nhad_RnD_sig, display=False)
glue("mean_nhad_BB1_sig", mean_nhad_BB1_sig, display=False)
glue("mean_nhad_RnD_bkg", mean_nhad_RnD_bkg, display=False)
glue("mean_nhad_BB1_bkg", mean_nhad_BB1_bkg, display=False)


Como se puede ver en la {numref}`rawdata-nhadrones`, el conjunto R&D posee una media de {glue:text}`mean_nhad_RnD_sig:.0f` hadrones por evento para la señal, y de {glue:text}`mean_nhad_RnD_bkg:.0f` hadrones por evento para el fondo. El conjunto BB1 es similar, con una media de {glue:text}`mean_nhad_BB1_sig:.0f` y {glue:text}`mean_nhad_BB1_bkg:.0f` hadrones por evento para señal y fondo, respectivamente. En general, los eventos de señal producen menos hadrones. Esto está relacionado con la naturaleza de los eventos; los eventos de fondo poseen más hadrones por evento que los de señal, porque en general provienen de jets de gluones, que generan más radiación de partículas{cite}`Aad_2014`.

Las distribuciones de la media de las variables $pT$, $\eta$ y $\phi$ por evento se pueden ver en las {numref}`rawdata-meanRnD` y {numref}`rawdata-meanBB1`, para el conjunto R&D y el conjunto BB1, respectivamente.

In [7]:
# En esta celda graficamos la distribución del valor medio de pT, eta y phi de cada evento.

# Cada 3 valores es pT, cada 3 empezando por 1 es eta 
# y cada 3 empezando por 2 es phi.
# Remplazamos los ceros con NaN para poder utilizar .mean()
for name, ns_df, df, nbins in zip(['R&D', 'BB1'], [ns_df_RnD, ns_df_BB1], [df_RnD,df_BB1], [50,20]):
    pt_df = ns_df.iloc[:,::3].replace(0, np.NaN)
    eta_df = ns_df.iloc[:,1::3].replace(0, np.NaN)
    phi_df = ns_df.iloc[:,2::3].replace(0, np.NaN)

    # Calculamos la media de cada evento
    df['mean_pT'] = pt_df.mean(axis=1)
    df['mean_eta']= eta_df.mean(axis=1)
    df['mean_phi']= phi_df.mean(axis=1)

    # Graficamos cada variable
    variables = ['mean_pT', 'mean_eta', 'mean_phi']
    names = [r'$\langle p_T\rangle$ de las partículas',r'$\langle\eta\rangle$ de las partículas', r'$\langle\phi\rangle$ de las partículas']
    for variable, name_var in zip(variables,names):
        fig = plt.figure(facecolor='white')
        bkg_sig_hist(df, variable, label=2100, xlabel=name_var, ylabel='Densidad de eventos', n_bins=nbins)
        plt.title(r'{}: Distribución de '.format(name)+name_var)
        plt.savefig(os.path.join('../../figuras/','rawdata-{}-{}.png'.format(variable,name)), bbox_inches='tight', facecolor=fig.get_facecolor(),edgecolor='none')
        plt.clf()

# Creamos un grid para RnD
imagenes = ['./../../figuras/rawdata-mean_pT-R&D.png', 
'./../../figuras/rawdata-mean_eta-R&D.png',
'./../../figuras/rawdata-mean_phi-R&D.png']
image_grid(rows=1, columns=3, images=imagenes, name='rawdata-means-RnD', path=PATH_IMAGES, remove=True)

# Creamos un grid para BB1
imagenes = ['./../../figuras/rawdata-mean_pT-BB1.png', 
'./../../figuras/rawdata-mean_eta-BB1.png',
'./../../figuras/rawdata-mean_phi-BB1.png']
image_grid(rows=1, columns=3, images=imagenes, name='rawdata-means-BB1', path=PATH_IMAGES, remove=True)

<Figure size 432x288 with 0 Axes>

<Figure size 432x288 with 0 Axes>

<Figure size 432x288 with 0 Axes>

<Figure size 432x288 with 0 Axes>

<Figure size 432x288 with 0 Axes>

...

<Figure size 432x288 with 0 Axes>

<Figure size 432x288 with 0 Axes>

<Figure size 432x288 with 0 Axes>

<Figure size 432x288 with 0 Axes>

<Figure size 432x288 with 0 Axes>

```{figure} ./../../figuras/rawdata-means-RnD.png
---
name: rawdata-meanRnD
width: 100%
---
Distribución de la media de $pT$, $\eta$ y $\phi$ para las partículas de los eventos del conjunto R&D.
```

```{figure} ./../../figuras/rawdata-means-BB1.png
---
name: rawdata-meanBB1
width: 100%
---
Distribución de la media de $pT$, $\eta$ y $\phi$ para las partículas de los eventos del conjunto BB1.
```

In [8]:
# En esta celda calculamos los valores medios de pT de las figuras anteriores
meanpt_sig_RnD = df_RnD.loc[df_RnD.iloc[:,2100]==1]['mean_pT'].mean()
meanpt_bkg_RnD = df_RnD.loc[df_RnD.iloc[:,2100]==0]['mean_pT'].mean()
meanpt_sig_BB1 = df_BB1.loc[df_BB1.iloc[:,2100]==1]['mean_pT'].mean()
meanpt_bkg_BB1 = df_BB1.loc[df_BB1.iloc[:,2100]==0]['mean_pT'].mean()

glue("meanpt_sig_RnD", meanpt_sig_RnD, display=False)
glue("meanpt_bkg_RnD", meanpt_bkg_RnD , display=False)
glue("meanpt_sig_BB1", meanpt_sig_BB1, display=False)
glue("meanpt_bkg_BB1", meanpt_bkg_BB1, display=False)

Las distribuciones de la señal son más claras en la {numref}`rawdata-meanRnD` que en la {numref}`rawdata-meanBB1`, debido a que hay mayor cantidad de eventos de señal. $\phi$ y $\eta$ no parecen diferir notablemente entre eventos de señal y fondo. Sin embargo, se observa que los valores de $pT$ difieren, siendo el $pT$ de los eventos de señal mayor que el $pT$ de los eventos de fondo, debido a que se requiere una mayor transferencia de momento para crear la partícula de nueva física.

En el caso del conjunto R&D, se tiene una media de $pT$ de {glue:text}`meanpt_sig_RnD:.0f` y {glue:text}`meanpt_bkg_RnD:.0f` GeV para señal y fondo, respectivamente. Para el conjunto BB1 las medias son de {glue:text}`meanpt_sig_BB1:.0f` y {glue:text}`meanpt_bkg_BB1:.0f` GeV. En general, la media de $pT$ de los eventos de señal es mayor.

Para poder entender los procesos físicos de los eventos, es necesario agrupar los datos en jets. Esto se hará en la siguiente sección.